In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0         conda-forge
    geopy:         1.18.1-py_0       conda-forge

The following packages will be UPDATED:

    openssl:       1.0.2p-h470a237_1 conda-forge --> 1.0.2p-h470a237_2 conda-forge

Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - folium=0.5.0


The following NEW packages will be INSTALLED:

    altair:  2.3.0-py36_1001 conda-forge
    branca:  0.3.1-py_0      conda-forge
    folium:  0.5.0-py_0      conda-forge
    vincent: 0.4.4-py_1      conda-forge

Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Libraries imported.


In [138]:
import requests
import csv
from bs4 import BeautifulSoup
page= requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

raw_list = pd.read_html(page, header=0, attrs={"class":"wikitable sortable"})[0]

In [139]:
raw_list.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [140]:
raw = raw_list.groupby(['Postcode','Borough'],as_index=False, sort=False,).agg(lambda x: ','.join(set(x)))
raw.loc[:, 'Borough'].replace('Not assigned', np.nan, inplace=True)
raw.dropna(subset=['Borough'], inplace=True)
raw.reset_index(drop=True, inplace=True)
raw

Postcode           Borough  \
0        M3A        North York   
1        M4A        North York   
2        M5A  Downtown Toronto   
3        M6A        North York   
4        M7A      Queen's Park   
5        M9A         Etobicoke   
6        M1B       Scarborough   
7        M3B        North York   
8        M4B         East York   
9        M5B  Downtown Toronto   
10       M6B        North York   
11       M9B         Etobicoke   
12       M1C       Scarborough   
13       M3C        North York   
14       M4C         East York   
15       M5C  Downtown Toronto   
16       M6C              York   
17       M9C         Etobicoke   
18       M1E       Scarborough   
19       M4E      East Toronto   
20       M5E  Downtown Toronto   
21       M6E              York   
22       M1G       Scarborough   
23       M4G         East York   
24       M5G  Downtown Toronto   
25       M6G  Downtown Toronto   
26       M1H       Scarborough   
27       M2H        North York   
28       M3H        North York   
29       M4H         East York   
30       M5H  Downtown Toronto   
31       M6H      West Toronto   
32       M1J       Scarborough   
33       M2J        North York   
34       M3J        North York   
35       M4J         East York   
36       M5J  Downtown Toronto   
37       M6J      West Toronto   
38       M1K       Scarborough   
39       M2K        North York   
40       M3K        North York   
41       M4K      East Toronto   
42       M5K  Downtown Toronto   
43       M6K      West Toronto   
44       M1L       Scarborough   
45       M2L        North York   
46       M3L        North York   
47       M4L      East Toronto   
48       M5L  Downtown Toronto   
49       M6L        North York   
50       M9L        North York   
51       M1M       Scarborough   
52       M2M        North York   
53       M3M        North York   
54       M4M      East Toronto   
55       M5M        North York   
56       M6M              York   
57       M9M        North York   
58       M1N       Scarborough   
59       M2N        North York   
60       M3N        North York   
61       M4N   Central Toronto   
62       M5N   Central Toronto   
63       M6N              York   
64       M9N              York   
65       M1P       Scarborough   
66       M2P        North York   
67       M4P   Central Toronto   
68       M5P   Central Toronto   
69       M6P      West Toronto   
70       M9P         Etobicoke   
71       M1R       Scarborough   
72       M2R        North York   
73       M4R   Central Toronto   
74       M5R   Central Toronto   
75       M6R      West Toronto   
76       M7R       Mississauga   
77       M9R         Etobicoke   
78       M1S       Scarborough   
79       M4S   Central Toronto   
80       M5S  Downtown Toronto   
81       M6S      West Toronto   
82       M1T       Scarborough   
83       M4T   Central Toronto   
84       M5T  Downtown Toronto   
85       M1V       Scarborough   
86       M4V   Central Toronto   
87       M5V  Downtown Toronto   
88       M8V         Etobicoke   
89       M9V         Etobicoke   
90       M1W       Scarborough   
91       M4W  Downtown Toronto   
92       M5W  Downtown Toronto   
93       M8W         Etobicoke   
94       M9W         Etobicoke   
95       M1X       Scarborough   
96       M4X  Downtown Toronto   
97       M5X  Downtown Toronto   
98       M8X         Etobicoke   
99       M4Y  Downtown Toronto   
100      M7Y      East Toronto   
101      M8Y         Etobicoke   
102      M8Z         Etobicoke   

                                         Neighbourhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                             Harbourfront,Regent Park  
3                      Lawrence Manor,Lawrence Heights  
4                                         Not assigned  
5                                     Islington Avenue  
6                                        Malvern,Rouge  
7          

In [141]:
raw.shape 

(103, 3)

# part 2

In [142]:
GDF = pd.read_csv('http://cocl.us/Geospatial_data/Geospatial_Coordinates.csv')
GDF

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
5           M1J  43.744734 -79.239476
6           M1K  43.727929 -79.262029
7           M1L  43.711112 -79.284577
8           M1M  43.716316 -79.239476
9           M1N  43.692657 -79.264848
10          M1P  43.757410 -79.273304
11          M1R  43.750072 -79.295849
12          M1S  43.794200 -79.262029
13          M1T  43.781638 -79.304302
14          M1V  43.815252 -79.284577
15          M1W  43.799525 -79.318389
16          M1X  43.836125 -79.205636
17          M2H  43.803762 -79.363452
18          M2J  43.778517 -79.346556
19          M2K  43.786947 -79.385975
20          M2L  43.757490 -79.374714
21          M2M  43.789053 -79.408493
22          M2N  43.770120 -79.408493
23          M2P  43.752758 -79.400049
24          M2R  43.782736 -79.442259
25          M3A  43.753259 -79.329656
26          M3B  43.745906 -79.352188
27          M3C  43.725900 -79.340923
28          M3H  43.754328 -79.442259
29          M3J  43.767980 -79.487262
30          M3K  43.737473 -79.464763
31          M3L  43.739015 -79.506944
32          M3M  43.728496 -79.495697
33          M3N  43.761631 -79.520999
34          M4A  43.725882 -79.315572
35          M4B  43.706397 -79.309937
36          M4C  43.695344 -79.318389
37          M4E  43.676357 -79.293031
38          M4G  43.709060 -79.363452
39          M4H  43.705369 -79.349372
40          M4J  43.685347 -79.338106
41          M4K  43.679557 -79.352188
42          M4L  43.668999 -79.315572
43          M4M  43.659526 -79.340923
44          M4N  43.728020 -79.388790
45          M4P  43.712751 -79.390197
46          M4R  43.715383 -79.405678
47          M4S  43.704324 -79.388790
48          M4T  43.689574 -79.383160
49          M4V  43.686412 -79.400049
50          M4W  43.679563 -79.377529
51          M4X  43.667967 -79.367675
52          M4Y  43.665860 -79.383160
53          M5A  43.654260 -79.360636
54          M5B  43.657162 -79.378937
55          M5C  43.651494 -79.375418
56          M5E  43.644771 -79.373306
57          M5G  43.657952 -79.387383
58          M5H  43.650571 -79.384568
59          M5J  43.640816 -79.381752
60          M5K  43.647177 -79.381576
61          M5L  43.648198 -79.379817
62          M5M  43.733283 -79.419750
63          M5N  43.711695 -79.416936
64          M5P  43.696948 -79.411307
65          M5R  43.672710 -79.405678
66          M5S  43.662696 -79.400049
67          M5T  43.653206 -79.400049
68          M5V  43.628947 -79.394420
69          M5W  43.646435 -79.374846
70          M5X  43.648429 -79.382280
71          M6A  43.718518 -79.464763
72          M6B  43.709577 -79.445073
73          M6C  43.693781 -79.428191
74          M6E  43.689026 -79.453512
75          M6G  43.669542 -79.422564
76          M6H  43.669005 -79.442259
77          M6J  43.647927 -79.419750
78          M6K  43.636847 -79.428191
79          M6L  43.713756 -79.490074
80          M6M  43.691116 -79.476013
81          M6N  43.673185 -79.487262
82          M6P  43.661608 -79.464763
83          M6R  43.648960 -79.456325
84          M6S  43.651571 -79.484450
85          M7A  43.662301 -79.389494
86          M7R  43.636966 -79.615819
87          M7Y  43.662744 -79.321558
88          M8V  43.605647 -79.501321
89          M8W  43.602414 -79.543484
90          M8X  43.653654 -79.506944
91          M8Y  43.636258 -79.498509
92          M8Z  43.628841 -79.520999
93          M9A  43.667856 -79.532242
94          M9B  43.650943 -79.554724
95          M9C  43.643515 -79.577201
96          M9L  43.756303 -79.565963
97          M9M  43.724766 -79.532242
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

In [143]:
GDF.rename(columns = {'Postal Code':'Postcode'}, inplace = True)
raw.reset_index(drop=True, inplace=True)
GDF.reset_index(drop=True, inplace=True)
raw = raw.astype(str)
GDF = GDF.astype(str)
GDF2 = pd.merge(raw, GDF, on = 'Postcode')
GDF2['Latitude'] = pd.to_numeric(GDF2['Latitude'], errors='coerce')
GDF2['Longitude'] = pd.to_numeric(GDF2['Longitude'], errors='coerce')
GDF2

Postcode           Borough  \
0        M3A        North York   
1        M4A        North York   
2        M5A  Downtown Toronto   
3        M6A        North York   
4        M7A      Queen's Park   
5        M9A         Etobicoke   
6        M1B       Scarborough   
7        M3B        North York   
8        M4B         East York   
9        M5B  Downtown Toronto   
10       M6B        North York   
11       M9B         Etobicoke   
12       M1C       Scarborough   
13       M3C        North York   
14       M4C         East York   
15       M5C  Downtown Toronto   
16       M6C              York   
17       M9C         Etobicoke   
18       M1E       Scarborough   
19       M4E      East Toronto   
20       M5E  Downtown Toronto   
21       M6E              York   
22       M1G       Scarborough   
23       M4G         East York   
24       M5G  Downtown Toronto   
25       M6G  Downtown Toronto   
26       M1H       Scarborough   
27       M2H        North York   
28       M3H        North York   
29       M4H         East York   
30       M5H  Downtown Toronto   
31       M6H      West Toronto   
32       M1J       Scarborough   
33       M2J        North York   
34       M3J        North York   
35       M4J         East York   
36       M5J  Downtown Toronto   
37       M6J      West Toronto   
38       M1K       Scarborough   
39       M2K        North York   
40       M3K        North York   
41       M4K      East Toronto   
42       M5K  Downtown Toronto   
43       M6K      West Toronto   
44       M1L       Scarborough   
45       M2L        North York   
46       M3L        North York   
47       M4L      East Toronto   
48       M5L  Downtown Toronto   
49       M6L        North York   
50       M9L        North York   
51       M1M       Scarborough   
52       M2M        North York   
53       M3M        North York   
54       M4M      East Toronto   
55       M5M        North York   
56       M6M              York   
57       M9M        North York   
58       M1N       Scarborough   
59       M2N        North York   
60       M3N        North York   
61       M4N   Central Toronto   
62       M5N   Central Toronto   
63       M6N              York   
64       M9N              York   
65       M1P       Scarborough   
66       M2P        North York   
67       M4P   Central Toronto   
68       M5P   Central Toronto   
69       M6P      West Toronto   
70       M9P         Etobicoke   
71       M1R       Scarborough   
72       M2R        North York   
73       M4R   Central Toronto   
74       M5R   Central Toronto   
75       M6R      West Toronto   
76       M7R       Mississauga   
77       M9R         Etobicoke   
78       M1S       Scarborough   
79       M4S   Central Toronto   
80       M5S  Downtown Toronto   
81       M6S      West Toronto   
82       M1T       Scarborough   
83       M4T   Central Toronto   
84       M5T  Downtown Toronto   
85       M1V       Scarborough   
86       M4V   Central Toronto   
87       M5V  Downtown Toronto   
88       M8V         Etobicoke   
89       M9V         Etobicoke   
90       M1W       Scarborough   
91       M4W  Downtown Toronto   
92       M5W  Downtown Toronto   
93       M8W         Etobicoke   
94       M9W         Etobicoke   
95       M1X       Scarborough   
96       M4X  Downtown Toronto   
97       M5X  Downtown Toronto   
98       M8X         Etobicoke   
99       M4Y  Downtown Toronto   
100      M7Y      East Toronto   
101      M8Y         Etobicoke   
102      M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                             Harbourfront,Regent Park  43.654260 -79.360636  
3                      Lawrence Manor,Lawrence Heights  43.718518 -79.464763  
4                                         Not assigned  43.662301 -79.38

# part 3

In [144]:
print('The dataframe has {} boroughs and {} Neighbourhood.'.format(
        len(GDF2['Borough'].unique()),
        GDF2.shape[0]
    )
)

The dataframe has 11 boroughs and 103 Neighbourhood.


In [145]:

address = 'Toronto'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/ipykernel_launcher.py:4: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  after removing the cwd from sys.path.


The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [146]:
Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)
for lat, lng, borough, Neighbourhood in zip(GDF2['Latitude'], GDF2['Longitude'], GDF2['Borough'], GDF2['Neighbourhood']):
    label = '{}, {}'.format(Neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.5,
        parse_html=False).add_to(map_toronto)  
  
Toronto

In [153]:
CLIENT_ID = 'RHYEME5RQEKDELM3BX2VMMPC0FIQGHTEB1P10JUYUBKSGTXD' # your Foursquare ID
CLIENT_SECRET = 'ZK5SGWTND54B0IRBZHKFS0MO10XEMWWFAGI41YPFPF121QO0' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 100
raduis = 500
latitude = latitude
longitude = longitude
search_query = address

url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, LIMIT, raduis)
url

'https://api.foursquare.com/v2/venues/search?client_id=RHYEME5RQEKDELM3BX2VMMPC0FIQGHTEB1P10JUYUBKSGTXD&client_secret=ZK5SGWTND54B0IRBZHKFS0MO10XEMWWFAGI41YPFPF121QO0&ll=43.653963,-79.387207&v=20180604&query=Toronto&radius=100&limit=500'

In [154]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [155]:
toronto_venues = getNearbyVenues(names = GDF2['Neighbourhood'], latitudes = GDF2['Latitude'], longitudes = GDF2['Longitude'], radius=500)

Parkwoods
Victoria Village
Harbourfront,Regent Park
Lawrence Manor,Lawrence Heights
Not assigned
Islington Avenue
Malvern,Rouge
Don Mills North
Woodbine Gardens,Parkview Hill
Ryerson,Garden District
Glencairn
Princess Gardens,West Deane Park,Martin Grove,Islington,Cloverdale
Highland Creek,Rouge Hill,Port Union
Don Mills South,Flemingdon Park
Woodbine Heights
St. James Town
Humewood-Cedarvale
Markland Wood,Old Burnhamthorpe,Bloordale Gardens,Eringate
Morningside,Guildwood,West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Downsview North,Wilson Heights,Bathurst Manor
Thorncliffe Park
Adelaide,Richmond,King
Dovercourt Village,Dufferin
Scarborough Village
Fairview,Oriole,Henry Farm
Northwood Park,York University
East Toronto
Harbourfront East,Toronto Islands,Union Station
Little Portugal,Trinity
Ionview,Kennedy Park,East Birchmount Park
Bayview Village
CFB Toronto,Downsview East
Riverdale,The Danforth West
Design E

In [156]:
toronto_venues.shape


(2229, 7)

In [164]:
toronto_venues.groupby('Neighbourhood').count().reset_index()

Neighbourhood  Neighbourhood Latitude  \
0                              Adelaide,Richmond,King                     100   
1                                           Agincourt                       4   
2   Agincourt North,Steeles East,L'Amoreaux East,M...                       3   
3                               Alderwood,Long Branch                       9   
4                                     Bayview Village                       4   
5                    Bedford Park,Lawrence Manor East                      25   
6                                         Berczy Park                      55   
7    Business reply mail Processing Centre969 Eastern                      17   
8                          CFB Toronto,Downsview East                       4   
9                                 Caledonia-Fairbanks                       6   
10              Canada Post Gateway Processing Centre                      11   
11                                          Cedarbrae                       7   
12                                 Central Bay Street                      83   
13                                           Christie                      15   
14                               Church and Wellesley                      87   
15                         Cliffside West,Birch Cliff                       4   
16      Cliffside,Scarborough Village West,Cliffcrest                       2   
17                      Commerce Court,Victoria Hotel                     100   
18                                         Davisville                      33   
19                                   Davisville North                       6   
20            Design Exchange,Toronto Dominion Centre                     100   
21                                    Don Mills North                       6   
22                    Don Mills South,Flemingdon Park                      20   
23                        Dovercourt Village,Dufferin                      20   
24                                  Downsview Central                       2   
25      Downsview North,Wilson Heights,Bathurst Manor                      17   
26                                Downsview Northwest                       5   
27                                     Downsview West                       4   
28                                       East Toronto                       2   
29                                    Emery,Humberlea                       1   
30         Exhibition Place,Parkdale Village,Brockton                      18   
31                         Fairview,Oriole,Henry Farm                      60   
32                 Forest Hill West,Forest Hill North                       4   
33                                          Glencairn                       5   
34                      Golden Mile,Clairlea,Oakridge                       9   
35    Harbourfront East,Toronto Islands,Union Station                     100   
36                           Harbourfront,Regent Park                      48   
37                       High Park,The Junction South                      23   
38               Highland Creek,Rouge Hill,Port Union                       2   
39                                  Hillcrest Village                       4   
40                                      Humber Summit                       1   
41                                 Humewood-Cedarvale                       3   
42          Ionview,Kennedy Park,East Birchmount Park                       7   
43            Kensington Market,Grange Park,Chinatown                     100   
44  Kingsway Park South West,The Queensway West,Mi...                      13   
45                       L'Amoreaux West,Steeles West                      15   
46                    Lawrence Manor,Lawrence Heights                      14   
47                                      Lawrence Park                       5   
48                                            Leaside                  

In [166]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# in toronto_onehot found 'Neighborhood', so change it to 'Neighbor'
toronto_onehot.rename(columns = {'Neighbourhood':'Neighbor'}, inplace = True)

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0         Parkwoods                  0               0                  0   
1         Parkwoods                  0               0                  0   
2         Parkwoods                  0               0                  0   
3  Victoria Village                  0               0                  0   
4  Victoria Village                  0               0                  0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0            0           0                    0   
1                 0            0           0                    0   
2                 0            0           0                    0   
3                 0            0           0                    0   
4                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Beach  Beer Bar  Beer Store  \
0                 0                   0      0         0           0   
1                 0                   0      0         0           0   
2                 0                   0      0         0           0   
3                 0                   0      0         0           0   
4                 0                   0      0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0                   0          0       0           0              0   
1                   0          0       0           0              0   
2                   0          0       0           0              0   
3                   0          0       0           0              0   
4                   0          0       0           0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bubble Te

In [170]:

toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                              Adelaide,Richmond,King           0.000000   
1                                           Agincourt           0.000000   
2   Agincourt North,Steeles East,L'Amoreaux East,M...           0.000000   
3                               Alderwood,Long Branch           0.000000   
4                                     Bayview Village           0.000000   
5                    Bedford Park,Lawrence Manor East           0.000000   
6                                         Berczy Park           0.000000   
7    Business reply mail Processing Centre969 Eastern           0.000000   
8                          CFB Toronto,Downsview East           0.000000   
9                                 Caledonia-Fairbanks           0.000000   
10              Canada Post Gateway Processing Centre           0.000000   
11                                          Cedarbrae           0.000000   
12                                 Central Bay Street           0.000000   
13                                           Christie           0.000000   
14                               Church and Wellesley           0.000000   
15                         Cliffside West,Birch Cliff           0.000000   
16      Cliffside,Scarborough Village West,Cliffcrest           0.000000   
17                      Commerce Court,Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20            Design Exchange,Toronto Dominion Centre           0.000000   
21                                    Don Mills North           0.000000   
22                    Don Mills South,Flemingdon Park           0.000000   
23                        Dovercourt Village,Dufferin           0.000000   
24                                  Downsview Central           0.000000   
25      Downsview North,Wilson Heights,Bathurst Manor           0.000000   
26                                Downsview Northwest           0.000000   
27                                     Downsview West           0.000000   
28                                       East Toronto           0.000000   
29                                    Emery,Humberlea           0.000000   
30         Exhibition Place,Parkdale Village,Brockton           0.000000   
31                         Fairview,Oriole,Henry Farm           0.000000   
32                 Forest Hill West,Forest Hill North           0.000000   
33                                          Glencairn           0.000000   
34                      Golden Mile,Clairlea,Oakridge           0.000000   
35    Harbourfront East,Toronto Islands,Union Station           0.000000   
36                           Harbourfront,Regent Park           0.000000   
37                       High Park,The Junction South           0.000000   
38               Highland Creek,Rouge Hill,Port Union           0.000000   
39                                  Hillcrest Village           0.000000   
40                                      Humber Summit           0.000000   
41                                 Humewood-Cedarvale           0.000000   
42          Ionview,Kennedy Park,East Birchmount Park           0.000000   
43            Kensington Market,Grange Park,Chinatown           0.000000   
44  Kingsway Park South West,The Queensway West,Mi...           0.000000   
45                       L'Amoreaux West,Steeles West           0.000000   
46                    Lawrence Manor,Lawrence Heights           0.071429   
47                                      Lawrence Park           0.000000   
48                                            Leaside           0.000000   
49                            Little Portugal,Trinity           0.000000   
50                                      Malvern,Rouge           0.000000   
51  Markland Wood,Old Burnhamthorpe,Bloordale Gard...           0.000000   
52         M

In [171]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,Richmond,King----
                 venue  freq
0          Coffee Shop  0.06
1                 Café  0.05
2      Thai Restaurant  0.04
3  American Restaurant  0.04
4           Steakhouse  0.04


----Agincourt----
                        venue  freq
0                Skating Rink  0.25
1              Sandwich Place  0.25
2              Breakfast Spot  0.25
3                      Lounge  0.25
4  Modern European Restaurant  0.00


----Agincourt North,Steeles East,L'Amoreaux East,Milliken----
                        venue  freq
0                  Playground  0.33
1                      Bakery  0.33
2                        Park  0.33
3           Accessories Store  0.00
4  Modern European Restaurant  0.00


----Alderwood,Long Branch----
            venue  freq
0     Pizza Place  0.22
1        Pharmacy  0.11
2             Gym  0.11
3  Sandwich Place  0.11
4             Pub  0.11


----Bayview Village----
                 venue  freq
0                 Café  0.25
1  Japanese Restaur

In [174]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighbourhood  \
0                              Adelaide,Richmond,King   
1                                           Agincourt   
2   Agincourt North,Steeles East,L'Amoreaux East,M...   
3                               Alderwood,Long Branch   
4                                     Bayview Village   
5                    Bedford Park,Lawrence Manor East   
6                                         Berczy Park   
7    Business reply mail Processing Centre969 Eastern   
8                          CFB Toronto,Downsview East   
9                                 Caledonia-Fairbanks   
10              Canada Post Gateway Processing Centre   
11                                          Cedarbrae   
12                                 Central Bay Street   
13                                           Christie   
14                               Church and Wellesley   
15                         Cliffside West,Birch Cliff   
16      Cliffside,Scarborough Village West,Cliffcrest   
17                      Commerce Court,Victoria Hotel   
18                                         Davisville   
19                                   Davisville North   
20            Design Exchange,Toronto Dominion Centre   
21                                    Don Mills North   
22                    Don Mills South,Flemingdon Park   
23                        Dovercourt Village,Dufferin   
24                                  Downsview Central   
25      Downsview North,Wilson Heights,Bathurst Manor   
26                                Downsview Northwest   
27                                     Downsview West   
28                                       East Toronto   
29                                    Emery,Humberlea   
30         Exhibition Place,Parkdale Village,Brockton   
31                         Fairview,Oriole,Henry Farm   
32                 Forest Hill West,Forest Hill North   
33                                          Glencairn   
34                      Golden Mile,Clairlea,Oakridge   
35    Harbourfront East,Toronto Islands,Union Station   
36                           Harbourfront,Regent Park   
37                       High Park,The Junction South   
38               Highland Creek,Rouge Hill,Port Union   
39                                  Hillcrest Village   
40                                      Humber Summit   
41                                 Humewood-Cedarvale   
42          Ionview,Kennedy Park,East Birchmount Park   
43            Kensington Market,Grange Park,Chinatown   
44  Kingsway Park South West,The Queensway West,Mi...   
45                       L'Amoreaux West,Steeles West   
46                    Lawrence Manor,Lawrence Heights   
47                                      Lawrence Park   
48                                            Leaside   
49                            Little Portugal,Trinity   
50                                      Malvern,Rouge   
51  Markland Wood,Old Burnhamthorpe,Bloordale Gard...   
52         Mimico South,New Toronto,Humber Bay Shores   
53                    Morningside,Guildwood,West Hill   
54  Mount Olive,South Steeles,Thistletown,Silverst...   
55                                 North Toronto West   
56                                          Northwest   
57                     Northwood Park,York University   
58                                       Not assigned   
59                              Parkdale,Roncesvalles   
60                                          Parkwoods   
61  Princess Gardens,West Deane Park,Martin Grove,...   
62  Richview Gardens,Kingsview Village,St. Phillip...   
63                        Riverdale,The Danforth West   
64                                           Rosedale   
65                                           Roselawn   
66                            Ryerson,Garden District   
67  Scarborough Town Centre,Wexford Heights,Dorset...   
68                                Scarborough Village   
69        Silverthorn,Mount Dennis,Keelesdale,Del 

In [176]:
# set number of clusters
kclusters = 3

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_ [0:100]

array([2, 2, 0, 2, 2, 2, 2, 2, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 1, 2, 2, 2, 0, 1, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 2,
       2, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 1, 0, 2, 0, 1,
       2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 0, 2, 1, 2, 2, 2, 2, 0, 2, 2, 2, 0,
       2, 2, 0, 2, 2, 2, 2, 2, 2, 0, 2], dtype=int32)

In [181]:
#toronto_merged = toronto_data
toronto_merged = toronto_grouped

# add clustering labels
toronto_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(GDF2.set_index('Neighbourhood'), on='Neighbourhood')

# merge toronto_grouped with toronto_data to add 5th most categories
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')


toronto_merged # check the last columns!

Neighbourhood  Accessories Store  \
0                              Adelaide,Richmond,King           0.000000   
1                                           Agincourt           0.000000   
2   Agincourt North,Steeles East,L'Amoreaux East,M...           0.000000   
3                               Alderwood,Long Branch           0.000000   
4                                     Bayview Village           0.000000   
5                    Bedford Park,Lawrence Manor East           0.000000   
6                                         Berczy Park           0.000000   
7    Business reply mail Processing Centre969 Eastern           0.000000   
8                          CFB Toronto,Downsview East           0.000000   
9                                 Caledonia-Fairbanks           0.000000   
10              Canada Post Gateway Processing Centre           0.000000   
11                                          Cedarbrae           0.000000   
12                                 Central Bay Street           0.000000   
13                                           Christie           0.000000   
14                               Church and Wellesley           0.000000   
15                         Cliffside West,Birch Cliff           0.000000   
16      Cliffside,Scarborough Village West,Cliffcrest           0.000000   
17                      Commerce Court,Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20            Design Exchange,Toronto Dominion Centre           0.000000   
21                                    Don Mills North           0.000000   
22                    Don Mills South,Flemingdon Park           0.000000   
23                        Dovercourt Village,Dufferin           0.000000   
24                                  Downsview Central           0.000000   
25      Downsview North,Wilson Heights,Bathurst Manor           0.000000   
26                                Downsview Northwest           0.000000   
27                                     Downsview West           0.000000   
28                                       East Toronto           0.000000   
29                                    Emery,Humberlea           0.000000   
30         Exhibition Place,Parkdale Village,Brockton           0.000000   
31                         Fairview,Oriole,Henry Farm           0.000000   
32                 Forest Hill West,Forest Hill North           0.000000   
33                                          Glencairn           0.000000   
34                      Golden Mile,Clairlea,Oakridge           0.000000   
35    Harbourfront East,Toronto Islands,Union Station           0.000000   
36                           Harbourfront,Regent Park           0.000000   
37                       High Park,The Junction South           0.000000   
38               Highland Creek,Rouge Hill,Port Union           0.000000   
39                                  Hillcrest Village           0.000000   
40                                      Humber Summit           0.000000   
41                                 Humewood-Cedarvale           0.000000   
42          Ionview,Kennedy Park,East Birchmount Park           0.000000   
43            Kensington Market,Grange Park,Chinatown           0.000000   
44  Kingsway Park South West,The Queensway West,Mi...           0.000000   
45                       L'Amoreaux West,Steeles West           0.000000   
46                    Lawrence Manor,Lawrence Heights           0.071429   
47                                      Lawrence Park           0.000000   
48                                            Leaside           0.000000   
49                            Little Portugal,Trinity           0.000000   
50                                      Malvern,Rouge           0.000000   
51  Markland Wood,Old Burnhamthorpe,Bloordale Gard...           0.000000   
52         M

In [191]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

TypeError: must be real number, not str

In [185]:

toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Accessories Store  Airport Food Court  Airport Gate  Airport Lounge  \
2                 0.0                 0.0           0.0             0.0   
8                 0.0                 0.0           0.0             0.0   
9                 0.0                 0.0           0.0             0.0   
28                0.0                 0.0           0.0             0.0   
32                0.0                 0.0           0.0             0.0   
47                0.0                 0.0           0.0             0.0   
60                0.0                 0.0           0.0             0.0   
62                0.0                 0.0           0.0             0.0   
64                0.0                 0.0           0.0             0.0   
76                0.0                 0.0           0.0             0.0   
83                0.0                 0.0           0.0             0.0   
87                0.0                 0.0           0.0             0.0   
90                0.0                 0.0           0.0             0.0   
97                0.0                 0.0           0.0             0.0   

    Airport Service  Airport Terminal  American Restaurant  Antique Shop  \
2               0.0               0.0                  0.0           0.0   
8               0.0               0.0                  0.0           0.0   
9               0.0               0.0                  0.0           0.0   
28              0.0               0.0                  0.0           0.0   
32              0.0               0.0                  0.0           0.0   
47              0.0               0.0                  0.0           0.0   
60              0.0               0.0                  0.0           0.0   
62              0.0               0.0                  0.0           0.0   
64              0.0               0.0                  0.0           0.0   
76              0.0               0.0                  0.0           0.0   
83              0.0               0.0                  0.0           0.0   
87              0.0               0.0                  0.0           0.0   
90              0.0               0.0                  0.0           0.0   
97              0.0               0.0                  0.0           0.0   

    Aquarium  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
2        0.0               0.0          0.0         0.0                  0.0   
8        0.0               0.0          0.0         0.0                  0.0   
9        0.0               0.0          0.0         0.0                  0.0   
28       0.0               0.0          0.0         0.0                  0.0   
32       0.0               0.0          0.0         0.0                  0.0   
47       0.0               0.0          0.0         0.0                  0.0   
60       0.0               0.0          0.0         0.0                  0.0   
62       0.0               0.0          0.0         0.0                  0.0   
64       0.0               0.0          0.0         0.0                  0.0   
76       0.0               0.0          0.0         0.0                  0.0   
83       0.0               0.0          0.0         0.0                  0.0   
87       0.0               0.0          0.0         0.0                  0.0   
90       0.0               0.0          0.0         0.0                  0.0   
97       0.0               0.0          0.0         0.0                  0.0   

    Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  \
2                0.0                 0.0            0.0        0.0   
8                0.0                 0.0            0.0        0.0   
9                0.0                 0.0            0.0        0.0   
28               0.0                 0.0            0.0        0.0   
32               0.0                 0.0            0.0        0.0   
47               0.0                 0.0            0.0        0.0   
60               0.0                 0.0      

In [186]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Accessories Store  Airport Food Court  Airport Gate  Airport Lounge  \
24                0.0                 0.0           0.0             0.0   
29                0.0                 0.0           0.0             0.0   
40                0.0                 0.0           0.0             0.0   
61                0.0                 0.0           0.0             0.0   
65                0.0                 0.0           0.0             0.0   
68                0.0                 0.0           0.0             0.0   
78                0.0                 0.0           0.0             0.0   

    Airport Service  Airport Terminal  American Restaurant  Antique Shop  \
24              0.0               0.0                  0.0           0.0   
29              0.0               0.0                  0.0           0.0   
40              0.0               0.0                  0.0           0.0   
61              0.0               0.0                  0.0           0.0   
65              0.0               0.0                  0.0           0.0   
68              0.0               0.0                  0.0           0.0   
78              0.0               0.0                  0.0           0.0   

    Aquarium  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
24       0.0               0.0          0.0         0.0                  0.0   
29       0.0               0.0          0.0         0.0                  0.0   
40       0.0               0.0          0.0         0.0                  0.0   
61       0.0               0.0          0.0         0.0                  0.0   
65       0.0               0.0          0.0         0.0                  0.0   
68       0.0               0.0          0.0         0.0                  0.0   
78       0.0               0.0          0.0         0.0                  0.0   

    Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  \
24               0.0                 0.0            0.0        0.0   
29               0.0                 0.0            0.0        0.0   
40               0.0                 0.0            0.0        0.0   
61               0.0                 0.0            0.0        0.0   
65               0.0                 0.0            0.0        0.0   
68               0.0                 0.0            0.0        0.0   
78               0.0                 0.0            0.0        0.0   

    Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
24         0.0         0.0     0.0   0.0  0.0             0.5   
29         0.0         0.0     0.0   0.0  0.0             1.0   
40         0.0         0.0     0.0   0.0  0.0             0.0   
61         0.0         0.0     0.0   1.0  0.0             0.0   
65         0.0         0.0     0.0   0.0  0.0             0.0   
68         0.0         0.0     0.0   0.0  0.0             0.0   
78         0.0         0.0     0.0   0.0  0.0             1.0   

    Baseball Stadium  Basketball Court  Basketball Stadium  Beach  Beer Bar  \
24               0.0               0.0                 0.0    0.0       0.0   
29               0.0               0.0                 0.0    0.0       0.0   
40               0.0               0.0                 0.0    0.0       0.0   
61               0.0               0.0                 0.0    0.0       0.0   
65               0.0               0.0                 0.0    0.0       0.0   
68               0.0               0.0                 0.0    0.0       0.0   
78               0.0               0.0                 0.0    0.0       0.0   

    Beer Store  Belgian Restaurant  Bike Shop  Bistro  Board Shop  \
24         0.0                 0.0        0.0     0.0         0.0   
29         0.0                 0.0        0.0     0.0         0.0   
40         0.0                 0.0        0.0     0.0         0.0   
61         0.0                 0.0        0.0     0.0         0.0   
65         0.0                 0.0        0.0     0.0         0.0   
68         0.0          

In [187]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Accessories Store  Airport Food Court  Airport Gate  Airport Lounge  \
0            0.000000            0.000000      0.000000        0.000000   
1            0.000000            0.000000      0.000000        0.000000   
3            0.000000            0.000000      0.000000        0.000000   
4            0.000000            0.000000      0.000000        0.000000   
5            0.000000            0.000000      0.000000        0.000000   
6            0.000000            0.000000      0.000000        0.000000   
7            0.000000            0.000000      0.000000        0.000000   
10           0.000000            0.000000      0.000000        0.000000   
11           0.000000            0.000000      0.000000        0.000000   
12           0.000000            0.000000      0.000000        0.000000   
13           0.000000            0.000000      0.000000        0.000000   
14           0.000000            0.000000      0.000000        0.000000   
15           0.000000            0.000000      0.000000        0.000000   
16           0.000000            0.000000      0.000000        0.000000   
17           0.000000            0.000000      0.000000        0.000000   
18           0.000000            0.000000      0.000000        0.000000   
19           0.000000            0.000000      0.000000        0.000000   
20           0.000000            0.000000      0.000000        0.000000   
21           0.000000            0.000000      0.000000        0.000000   
22           0.000000            0.000000      0.000000        0.000000   
23           0.000000            0.000000      0.000000        0.000000   
25           0.000000            0.000000      0.000000        0.000000   
26           0.000000            0.000000      0.000000        0.000000   
27           0.000000            0.000000      0.000000        0.000000   
30           0.000000            0.000000      0.000000        0.000000   
31           0.000000            0.000000      0.000000        0.000000   
33           0.000000            0.000000      0.000000        0.000000   
34           0.000000            0.000000      0.000000        0.000000   
35           0.000000            0.000000      0.000000        0.000000   
36           0.000000            0.000000      0.000000        0.000000   
37           0.000000            0.000000      0.000000        0.000000   
38           0.000000            0.000000      0.000000        0.000000   
39           0.000000            0.000000      0.000000        0.000000   
41           0.000000            0.000000      0.000000        0.000000   
42           0.000000            0.000000      0.000000        0.000000   
43           0.000000            0.000000      0.000000        0.000000   
44           0.000000            0.000000      0.000000        0.000000   
45           0.000000            0.000000      0.000000        0.000000   
46           0.071429            0.000000      0.000000        0.000000   
48           0.000000            0.000000      0.000000        0.000000   
49           0.000000            0.000000      0.000000        0.000000   
50           0.000000            0.000000      0.000000        0.000000   
51           0.000000            0.000000      0.000000        0.000000   
52           0.000000            0.000000      0.000000        0.000000   
53           0.000000            0.000000      0.000000        0.000000   
54           0.000000            0.000000      0.000000        0.000000   
55           0.000000            0.000000      0.000000        0.000000   
56           0.000000            0.000000      0.000000        0.000000   
57           0.000000            0.000000      0.000000        0.000000   
58           0.000000            0.000000      0.000000        0.000000   
59           0.000000            0.000000      0.000000        0.000000   
63           0.000000            0.000000      0.000000        0.000000   
66           0.000000        